One off conversion / data wrangling script, to avoid redownloading videos.

In [17]:
import pandas as pd
import base64

from tqdm import tqdm

In [16]:
df = pd.read_parquet("../data/dataset_original.parquet")

In [14]:
df.head()

video_id  frame_idx  timestamp                       image_path  \
0  8Ilh1ewceco          0        0.0    data/images/8Ilh1ewceco/0.jpg   
1  8Ilh1ewceco        145        5.0  data/images/8Ilh1ewceco/145.jpg   
2  8Ilh1ewceco        290       10.0  data/images/8Ilh1ewceco/290.jpg   
3  8Ilh1ewceco        435       15.0  data/images/8Ilh1ewceco/435.jpg   
4  8Ilh1ewceco        580       20.0  data/images/8Ilh1ewceco/580.jpg   

      dim_0     dim_1     dim_2     dim_3     dim_4     dim_5  ...   dim_502  \
0 -0.013127 -0.022996 -0.049374 -0.006306  0.013602 -0.003762  ... -0.006920   
1  0.009040  0.003338  0.029684 -0.033058  0.040864 -0.006447  ...  0.033575   
2  0.004891  0.006527  0.004417 -0.000323  0.006400 -0.024191  ... -0.043122   
3 -0.022159  0.020703 -0.021607 -0.019721 -0.006067 -0.035070  ... -0.017047   
4 -0.015903  0.033545  0.009257 -0.033540  0.010586 -0.028067  ... -0.016532   

    dim_503   dim_504   dim_505   dim_506   dim_507   dim_508   dim_509  \
0  0.013831  0.056647  0.007946 -0.002478 -0.030497 -0.011770  0.067427   
1 -0.019076  0.047166 -0.010574 -0.018608 -0.013465 -0.020017  0.086240   
2 -0.010695  0.005672  0.000172 -0.014442 -0.014647 -0.016840  0.100285   
3 -0.018341 -0.006733 -0.007040 -0.008368  0.009755 -0.045662  0.116601   
4  0.012388  0.020868 -0.012635  0.010914  0.009203 -0.010078  0.063971   

    dim_510   dim_511  
0 -0.031810 -0.025615  
1 -0.029653  0.035949  
2  0.013794  0.015046  
3 -0.000572 -0.000985  
4 -0.038024  0.025840  

[5 rows x 516 columns]

In [21]:
image_paths = df["image_path"].tolist()
new_df = df.rename(columns={"image_path": "base64_image"})
for i, img in enumerate(tqdm(image_paths)):
    with open(f"../{img}", "rb") as image_file:
        encoded_string = base64.b64encode(image_file.read()).decode()
    new_df.loc[i, "base64_image"] = encoded_string

100%|██████████| 71761/71761 [00:49<00:00, 1458.75it/s]


In [23]:
from pipeline.process_videos import DATAFRAME_PATH

new_df.to_parquet(DATAFRAME_PATH, index=False)

/Users/sidneyradcliffe/miniforge3/envs/visual-content-search-over-videos/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [24]:
# reload, check it's correct
new_df = pd.read_parquet(DATAFRAME_PATH)

In [25]:
new_df.head()

video_id  frame_idx  timestamp  \
0  8Ilh1ewceco          0        0.0   
1  8Ilh1ewceco        145        5.0   
2  8Ilh1ewceco        290       10.0   
3  8Ilh1ewceco        435       15.0   
4  8Ilh1ewceco        580       20.0   

                                        base64_image     dim_0     dim_1  \
0  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH... -0.013127 -0.022996   
1  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH...  0.009040  0.003338   
2  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH...  0.004891  0.006527   
3  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH... -0.022159  0.020703   
4  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH... -0.015903  0.033545   

      dim_2     dim_3     dim_4     dim_5  ...   dim_502   dim_503   dim_504  \
0 -0.049374 -0.006306  0.013602 -0.003762  ... -0.006920  0.013831  0.056647   
1  0.029684 -0.033058  0.040864 -0.006447  ...  0.033575 -0.019076  0.047166   
2  0.004417 -0.000323  0.006400 -0.024191  ... -0.043122 -0.010695  0.005672   
3 -0.021607 -0.019721 -0.006067 -0.035070  ... -0.017047 -0.018341 -0.006733   
4  0.009257 -0.033540  0.010586 -0.028067  ... -0.016532  0.012388  0.020868   

    dim_505   dim_506   dim_507   dim_508   dim_509   dim_510   dim_511  
0  0.007946 -0.002478 -0.030497 -0.011770  0.067427 -0.031810 -0.025615  
1 -0.010574 -0.018608 -0.013465 -0.020017  0.086240 -0.029653  0.035949  
2  0.000172 -0.014442 -0.014647 -0.016840  0.100285  0.013794  0.015046  
3 -0.007040 -0.008368  0.009755 -0.045662  0.116601 -0.000572 -0.000985  
4 -0.012635  0.010914  0.009203 -0.010078  0.063971 -0.038024  0.025840  

[5 rows x 516 columns]